# VWAP - Crossover

Stands for Volume Weight Moving Average. Does it cover the short coming for SMA by taking into volume information?

## Comment
As predicted, vwap behaves just like moving average. But it takes volume info into account, so it performed slightly better than moving average.

## Data

In [1]:
from btbox import *
from pandas import Series, DataFrame

In [2]:
SYMBOL = 'SPY'
START = '2000-01-01'
WINDOW = 500
INTERVAL = 1

In [3]:
dfs = {SYMBOL: import_yahoo_csv(f'../../_data_/{SYMBOL}_bar1day.csv')}

## Benchmark

In [4]:
class BM_AllInAndForget(Strategy):

    def initial(self, b: Broker):
        b.portfolio.trade_target_weight(SYMBOL, 1)


class BM_KeepAtHalf(Strategy):

    @interval(INTERVAL)
    def step(self, b: Broker):
        b.portfolio.trade_target_weight(SYMBOL, 0.5)

## Indicator

In [5]:
def cal_vwap_cross(short: int, long: int,
                   win: DataFrame) -> tuple[int | None, float, float]:

    def cal_vwap(period: int, ohlcv: DataFrame) -> Series:
        price = ohlcv.Close
        volume = ohlcv.Volume
        vwap = (price *
                volume).rolling(period).sum() / volume.rolling(period).sum()
        vwap = vwap.dropna()
        assert len(vwap) == 2
        return vwap

    vwap_short = cal_vwap(short, win.iloc[-short - 1:])
    vwap_long = cal_vwap(long, win.iloc[-long - 1:])
    vwap_diff = vwap_short - vwap_long
    cross = None
    if vwap_diff[-1] > 0 and vwap_diff[-2] < 0:
        cross = +1
    if vwap_diff[-1] < 0 and vwap_diff[-2] > 0:
        cross = -1
    return (cross, vwap_short[-1], vwap_long[-1])

## Strategy

In [6]:
def ST_VWAPCross(short: int, long: int):

    class ST(Strategy):
        name = f'ST_VWAPCross({short},{long})'

        @interval(INTERVAL)
        def step(self, b: Broker):
            win = b.market.get_ohlcv_window(SYMBOL)
            vwap_cross, vwap_short, vwap_long = cal_vwap_cross(
                short, long, win)
            if vwap_cross == +1:
                b.portfolio.trade_target_weight(SYMBOL, 1)
                self.journal.mark(+1, 'vwap-cross-up')
            if vwap_cross == -1:
                b.portfolio.trade_target_weight(SYMBOL, 0)
                self.journal.mark(-1, 'vwap-cross-down')
            self.journal.mark(vwap_short, 'vwap-short')
            self.journal.mark(vwap_long, 'vwap-long')

    return ST

## Backtest

In [7]:
bt = create_backtest(
    [
        BM_AllInAndForget,
        BM_KeepAtHalf,
        ST_VWAPCross(10, 20),
        ST_VWAPCross(20, 50),
        ST_VWAPCross(50, 200),
    ],
    dfs,
    start=START,
    window=WINDOW,
)

In [8]:
results = bt.run()

## Dashboard

In [9]:
results.dashboard_pretty()

## Equity Curve

In [10]:
results.plot()

## Review

In [11]:
results['ST_VWAPCross(50,200)'].journals[
    'vwap-short', 'vwap-long'].ffill.plot_line_on_price(SYMBOL)


In [12]:
results['ST_VWAPCross(50,200)'].journals[
    'vwap-cross-up', 'vwap-cross-down'].plot_scatter_on_price(SYMBOL)
